# TP2 - Compression, Prediction, Generation: Text Entropy

#### Stella Douka, Guillaume Charpiat 

#### Credits: Gaétan Marceau-Caron, Francesco Pezzicoli

### Introduction

In this TP we are interested in compressing and generating texts written in natural languages.
Given a text of length $n$, a sequence of symbols is just a vector $(x_1, . . . , x_n)$ where each $x_i$ is a symbol i.e. $x_i = a, b, c, \dots$. We can define the alphabet of possible symbols as $\mathcal{A} = \{a_1,a_2,\dots,a_M\}$ then each $x_i$ can have $M$ values.

In order to model the sequence of symbols we need a joint probability distribution for each symbol in the sequence, namely $p(X_1 = x_1, X_2 = x_2, \dots , X_n = x_n)$. If our alphabet had $M$ symbols, for modelling a sequence of length $n$ we would need $M^n$ probabilities. Thus some assumptions are required in order to reduce this dimensionality. In this case we will use two different models for $p$, the IID and the Markov Chain model.

### IID Model
The IID model assumes:

$$ p(X_1 = x_1, X_2 = x_2, \dots , X_n = x_n) = \prod_{i=1}^n p(X_i = x_i)$$

i.e. that the symbols in a sequence are independent and identically distributed. With this model we need only $M$ probabilities, one for each symbol. One can generalize and use symbols not of a single character but of multiples ones. For example using 3 characters per symbol, the symbols would be of the form $aaa,aab,...,zzz$. When using $k$ characters per symbols in an alphabet of $M$ characters, the needed probabilities would be $M^k$.


### Markov Chain Model

The Markov Chain model assume a limited range of dependence of the symbols. Indeed for an order $k$ Markov Chain:


$$p(X_i | X_{i-1},X_{i-2},\dots,X_1) = p(X_i | X_{i-1},X_{i-2},\dots,X_{i-k})$$


The meaning of the above structure is that the $i$-th symbol in the sequence depends only on the previous $k$ symbols. We add the time *invariant assumption*, meaning that the conditional probabilities do not depend on the time index $i$ i.e. $p(X_i | X_{i-1},X_{i-2},\dots,X_{i-k}) = p(X_{k+1} | X_{k},X_{k-1},\dots,X_{1})$. The most common and widely used Markov Chain is the Markov Chain of order 1:

$$p(X_i | X_{i-1},X_{i-2},\dots,X_1) = p(X_i | X_{i-1})$$

In this case the conditional probability $p(X_i|X_{i−1})$ can be expressed using $M^2$
numbers. Usually this is referred to as the *transition matrix*. Given an alphabet $\mathcal{A} = \{a_1,a_2,\dots,a_M\}$ the transition matrix can be written as: 

$$ \mathbb{M}_{kl} = p(X_i = a_k| X_{i-1} = a_l) $$

### Entropy and Cross-Entropy


- For the IID model of order 1 the entropy computation is straightforward: 
$$ H_{IID} = -\sum_{i=1}^M p(a_i) log p(a_i)$$ 
and consequently, starting from two distributions $p,q$ fitted on two different texts, the cross-entropy:
$$ CE_{IID} = -\sum_{i=1}^M p(a_i) log q(a_i)$$


- For the MC model of order 1 the entropy is defined as follows: 
$$ H_{MC} = - \sum_{kl} \pi(a_k) p(X_i = a_k| X_{i-1} = a_l) log \left(p(X_i = a_k| X_{i-1} = a_l)\right)= - \sum_{kl} \pi_k\mathbb{M}_{kl} log \mathbb{M}_{kl}$$
where $\pi$ is the stationary distribution of the Markov Chain i.e. $\pi_k = \mathbb{M}_{kl} \pi_l$. The code to compute the stationary distribution is already given.
The cross-entropy:
$$ CE_{IID} = - \sum_{kl} \pi_k\mathbb{M}_{kl} log \mathbb{M'}_{kl}$$
with $\mathbb{M}$ and $\mathbb{M'}$ are fitted on two different texts.


### Theoretical Questions: 

1) Interpret the time invariant assumption associated to our Markov chains in the contex of text generation.

2) How can we rewrite a Markov chain of higher order as a Markov chain of order 1?

3) Given a probability distribution over symbols, how to use it for generating sentences?

### Practical questions

In order to construct our IID and Markov Chain models we need some text. Our source will be a set of classical novels available at: https://www.lri.fr/~gcharpia/informationtheory/TP2_texts.zip

We will use the symbols in each text to learn the probabilities of each model. The alphabet we suggest for the characters to use is string.printable which is made of $\sim 100$ characters. (see below)

For both models, perform the following steps:

1) For different orders of dependencies, train the model on a novel and compute the associated entropy. What do you observe as the order increases? Explain your observations.

2) Use the other novels as test sets and compute the cross-entropy for each model trained previously. How to handle symbols (or sequences of symbols) not seen in the training set?

3) For each order of dependencies, compare the cross-entropy with the entropy. Explain and interpret the differences.

4) Choose the order of dependencies with the lowest cross-entropy and generate some sentences.

5) Train one model per novel and use the KL divergence in order to cluster the novels.


<b>Hints</b> : 

- In the MC case limit yourself to order $2$ (the computation can become quite expensive). If you have $ M \sim 100$ characters, for order $1$ you will need a $\sim 100 \times 100$ matrix, for order $2$ a $\sim 10^4 \times 10^4$ matrix.

- For the second order MC model you need to compute: $p(X_{i+1},X_{i}|X_{i},X_{i-1})$

- It is possible to implement efficiently the two models with dictionaries inPython.  For the IID model, a key of the dictionary is simply a symbol and the value is the number of occurrences of the symbol in the text. For a Markov chain, a key of the dictionary is also a symbol, but the value is a vector that contains the number of occurrences of each character of the alphabet.  Notice that a symbol may consist of one or several characters. Note also that there is no need to explicitly consider all possible symbols; the ones that are observed in the training set are sufficient.

- A low probability can be assigned to symbols not observed in the training-set.

#### Computing stationary distribution 

Here we provide you two version of the function to compute the stationary distirbution of a markov chain and show a small example

In [ ]:
#direct way to find pi (can be slow)
import  numpy  as np

def Compute_stationary_distribution(P_kl):
    ## P_kl must be the transition matrix from state l to state k!
    evals , evecs = np.linalg.eig(P_kl)   
    evec1 = evecs[:,np.isclose(evals , 1)]
    evec1 = evec1 [:,0]
    pi = evec1 / evec1.sum()
    pi = pi.real #stationary  probability
    
    return pi 

#iteative way (should be faster)
def Compute_stationary_distribution_it(P_kl, n_it):
    pi = np.random.uniform(size=P_kl.shape[0]) #initial state, can be a random one!
    pi /= pi.sum()
    #print(pi,pi.sum())
    for t in range(n_it):   
        pi = np.matmul(P_kl,pi)
    
    return pi

In [ ]:
##simple example of computation of stationary distribution 

n_it = 1000                                     ##remind to check that n_it is enough to reach convergence
P_kl = np.array([[0.7,0.5],[0.3,0.5]])
Compute_stationary_distribution_it(P_kl,n_it)

#### Defining the Alphabet

Example of uploading a text and filtering out characters which are not in the chosen alphabet

In [ ]:
import  string

def import_text(file_name):
    lines = []
    with  open(file_name , encoding='UTF8') as f:
        lines = f.readlines ()
        text = '\n'.join(lines)
        printable = set(string.printable)
        text = ''.join(filter(lambda x: x in printable , text))     
    return text

text = import_text('./texts/Alighieri.txt')

#### IID - MODEL

In [ ]:
import numpy as np
import math
from collections import Counter 

class IIDModel:
    """An interface for the text model"""
    def __init__(self, order=1):
        print("Creation of the model")
        self.order = order
        
    def process(self,text):
        ##...

    def getEntropy(self):
        ##...

    def getCrossEntropy(self, text):
        ##...
        
    def generate(self, length):
        ##...

In [ ]:
##clustering texts 

def KL_divergence(dist1,dist2): 
    ##...


#### MARKOV CHAIN - MODEL

In [ ]:
class MarkovModel:
    """An interface for the text model"""
    def __init__(self, order=2):
        print("Creation of the model")
        self.order = order

    def process(self, text):
        ##...

    def getEntropy(self):
        ##...
        
    def getCrossEntropy(self, text):
        ##...
    
    def generate(self, length):
        ##...